In [81]:
import random
from copy import deepcopy
import math
import matplotlib.pyplot as plt
import numpy as np

In [82]:
def load(file):
    cities = []
    with open(file, 'r') as f:
        for line in f:
            data = line.split()
            city_num = int(data[0])-1
            x = float(data[1])
            y = float(data[2])
            demand = float(data[3])
            ready_time = float(data[4])
            due_time = float(data[5])
            
            city = {'city_num' : city_num, 'x' : x, 'y' : y, 'demand' : demand, 'ready_time' : ready_time, 'due_time' : due_time}
            cities.append(city)
            
    return cities   

In [83]:
input1 = load('resources/input_1.txt')
input2 = load('resources/input_2.txt')
input3 = load('resources/input_3.txt')

for x in input1:
    print(x)

In [84]:
def calc_distance(city1, city2) -> float:
    return round(math.sqrt((city1["x"] - city2["x"])**2 + (city1["y"] - city2["y"])**2), 3)

In [85]:
remaining_cities = set(range(1, 100 + 1))
selection_value = [(i, max(calc_distance(input1[0], input1[i]), input1[i]["ready_time"])) 
                   for i in range(1, 100 + 1) if input1[i]["demand"] < 300]

selection_value.sort(key = lambda x: x[1])

for x in selection_value:
    print(x)

(59, 18.0)
(92, 18.385)
(42, 31.0)
(45, 32.0)
(14, 32.016)
(5, 34.0)
(63, 34.928)
(72, 35.0)
(27, 37.0)
(33, 37.0)
(28, 39.0)
(95, 39.0)
(36, 41.4)
(39, 44.0)
(83, 44.0)
(2, 50.0)
(31, 50.0)
(69, 50.0)
(47, 51.0)
(65, 51.0)
(52, 52.0)
(82, 55.0)
(62, 58.0)
(98, 58.0)
(15, 61.0)
(21, 62.0)
(12, 63.0)
(29, 63.0)
(11, 67.0)
(23, 68.0)
(44, 69.0)
(75, 69.0)
(30, 71.0)
(64, 73.0)
(76, 73.0)
(88, 74.0)
(16, 75.0)
(19, 76.0)
(61, 76.0)
(71, 77.0)
(73, 78.0)
(7, 81.0)
(38, 83.0)
(67, 83.0)
(99, 83.0)
(40, 85.0)
(18, 87.0)
(51, 88.0)
(85, 91.0)
(79, 92.0)
(87, 93.0)
(81, 94.0)
(86, 94.0)
(8, 95.0)
(53, 95.0)
(90, 95.0)
(78, 96.0)
(9, 97.0)
(22, 97.0)
(41, 97.0)
(6, 99.0)
(94, 100.0)
(57, 101.0)
(84, 101.0)
(49, 108.0)
(3, 116.0)
(34, 117.0)
(46, 117.0)
(10, 124.0)
(50, 124.0)
(20, 126.0)
(66, 127.0)
(56, 130.0)
(26, 132.0)
(43, 132.0)
(97, 133.0)
(37, 134.0)
(96, 135.0)
(55, 136.0)
(54, 140.0)
(32, 141.0)
(68, 142.0)
(35, 143.0)
(4, 149.0)
(74, 149.0)
(24, 153.0)
(17, 157.0)
(13, 159.0)
(91, 16

In [94]:
class Individual:
    def __init__(self, data, capacity, num_of_vehicles, num_of_cities, service_time):
        self.num_of_vehicles = num_of_vehicles
        self.num_of_cities = num_of_cities
        self.depot = data[0]
        self.data = data
        self.capacity = capacity
        self.service_time = service_time
        self.alpha = 2
        self.beta = 5
        self.solution = self.initial_solution_nearest_neighbors()
        self.fitness = self.calc_fitness()

    def __len__(self) -> int:
        return len(self.solution)
    
    def calc_distance(self, city1, city2) -> float:
        distance = math.sqrt((city1["x"] - city2["x"])**2 + (city1["y"] - city2["y"])**2)
        return round(distance, 3)

    def generate_solution(self):
        pass
    
    def generate_solution_random(self):
        routes = [[] for _ in range(self.num_of_vehicles)]
        remaining_cities = set(range(1, self.num_of_cities + 1))

        
        while remaining_cities:
            city_index = random.choice(list(remaining_cities))
            id = 0
            for j in range(self.num_of_vehicles):
                if self.route_is_valid(routes[j], city_index):
                    routes[j].append(city_index)
                    remaining_cities.remove(city_index)
                    id = 1
                    break
            if id == 0: #ako nije pronadjena feasible ruta, restartujemo alg
                routes = [[] for _ in range(self.num_of_vehicles)]
                remaining_cities = set(range(1, self.num_of_cities + 1))

        return self.make_chromosome(routes)


        
    def route_is_valid(self, route, city_index):
        fitness, current_time, remaining_capacity, _ = self.route_fitness(route)
        if not route:
            return True
        if fitness == float('inf') or current_time == float('inf') or remaining_capacity < self.data[city_index]["demand"] or \
           current_time + self.calc_distance(self.data[route[-1]], self.data[city_index]) > self.data[city_index]["due_time"]:
                    return False
        
        return True


    def initial_solution_nearest_neighbors(self):
        routes = [[] for _ in range(self.num_of_vehicles)]
        remaining_cities = set(range(1, self.num_of_cities + 1))
        
        return self.generate_solution_nearest_neighbors(routes, remaining_cities)
    
    def get_feasable_cities(self, remaining_cities, start_city, current_time, capacity):
            feasable_cities = [(i, max(self.calc_distance(self.data[start_city], self.data[i]), self.data[i]["ready_time"] - current_time)) 
                               for i in remaining_cities if current_time + self.calc_distance(self.data[start_city], self.data[i]) <= 
                                                            self.data[i]["due_time"] and capacity >= self.data[i]["demand"]]
            
            feasable_cities.sort(key = lambda x: x[1])
            return feasable_cities
    
    
    
    def generate_solution_nearest_neighbors(self, routes, remaining_cities):        
        j = 0
        while remaining_cities:
            feasable_cities = self.get_feasable_cities(remaining_cities, 0, 0, self.capacity)
            
            # for every route
            while True:
                if random.random() < 0.25:
                    city_index = random.choice(feasable_cities)
                else:
                    city_index = feasable_cities[0]

                city_index = city_index[0]  
                remaining_cities.remove(city_index)
                routes[j].append(city_index)

                fitness, current_time, remaining_capacity, is_unfeasable = self.route_fitness(routes[j])
                
                if is_unfeasable:
                    break
                
                feasable_cities = self.get_feasable_cities(remaining_cities, routes[j][-1], current_time, remaining_capacity)
                if not feasable_cities:
                    break
                                                      
            j = j + 1

        return self.make_chromosome(routes)

    def make_chromosome(self, routes):
        chromosome = []
        for i, route in enumerate(routes):
            for city in route:
                chromosome.append(city)
            chromosome.append(self.num_of_cities + i + 1)
        
        # remove empty routes
        for city in reversed(chromosome):
            if city > 100:
                chromosome.pop(-1)
            else:
                break

        return chromosome


    def generate_solution_sweep(self):
        pass

    def route_fitness(self, route):
        is_unfeasable = False
        if not route:
            return 0, 0, self.capacity, False
        
        fitness = 0
        current_time = 0
        current_city = self.depot
        remaining_capacity = self.capacity 
        for city_index in route:
            if current_time + self.calc_distance(current_city, self.data[city_index]) > self.data[city_index]["due_time"]:
                fitness += (self.calc_distance(current_city, self.data[city_index]) - self.data[city_index]["due_time"])*self.alpha
                is_unfeasable = True
            if remaining_capacity < self.data[city_index]["demand"]:
                fitness += (self.data[city_index]["demand"] - remaining_capacity)*self.beta
                is_unfeasable = True
                
            current_time += self.calc_distance(current_city, self.data[city_index]) + self.service_time
            current_city = self.data[city_index]
            remaining_capacity -= self.data[city_index]["demand"]
            
        fitness += current_time + self.calc_distance(self.data[route[-1]], self.depot)
        
        return fitness, current_time, remaining_capacity, is_unfeasable
    
    def get_routes(self):
        routes = []
        route = []
        # all routes except for the last route
        for city_index in self.solution:
            if city_index <= self.num_of_cities:
                route.append(city_index)
            else:
                if len(route) > 0:
                    routes.append(route)
                route = []

        # last route
        if len(route) > 0:
            routes.append(route)

        return routes
    
    def calc_fitness(self):
        routes = self.get_routes()
        
        # more routes than available vehicles
        if sum(1 for r in routes if len(r) > 0) > self.num_of_vehicles:
            return float('inf')

        fitness = 0
        for route in routes:
            if len(route) == 0:
                continue
            f, _, _, _ = self.route_fitness(route)
            fitness += f
            
        return fitness

        # distance ~ isto sto i vreme 
        # vreme na putu + vreme cekanja (ako ga ima) + service time 
        # vreme cekanja = 0 ili ready time - arrival time

        # Di + distance(i,j) + wait time

        # penalizujemo resenja koja ne ispunjavaju uslove za time window

    def is_feasable(self):
        routes = self.get_routes()
        if sum(1 for r in routes if len(r) > 0) > self.num_of_vehicles:
            print("more vehicles than available violation")
            return False
        

        visited_cities = [False for _ in range(self.num_of_cities)]

        for route in routes:
            current_time = 0
            current_city = 0
            remaining_capacity = self.capacity
            
            for city_index in route:
                if remaining_capacity < self.data[city_index]["demand"]:
                    print("capacity violation")
                    return False
                elif current_time + self.calc_distance(self.data[current_city], self.data[city_index]) > self.data[city_index]["due_time"]:
                    print("time window violation for route:", route)
                    return False
                else:
                    if visited_cities[city_index - 1]:
                        print("visiting same city multiple times violation")
                        return False
                    
                    current_time += self.calc_distance(self.data[current_city], self.data[city_index]) + self.service_time
                    remaining_capacity -= self.data[city_index]["demand"]
                    current_city = city_index
                    visited_cities[city_index - 1] = True
                    
        if not all(visited_cities):
            print("not all cities visited violation")
            return False
        
        return True

In [96]:
x = Individual(input1, 200, 50, 100, 10)
print(x.solution)
print(x.is_feasable())

y = Individual(input1, 200, 50, 100, 10)
print(y.solution)
print(y.is_feasable())

[59, 5, 83, 61, 85, 26, 4, 25, 101, 92, 42, 98, 16, 96, 97, 37, 13, 89, 58, 102, 88, 27, 12, 40, 74, 56, 77, 103, 45, 94, 99, 17, 91, 60, 100, 93, 104, 14, 15, 20, 32, 70, 105, 63, 62, 11, 90, 10, 1, 80, 106, 72, 39, 23, 67, 55, 54, 24, 107, 33, 69, 76, 79, 3, 48, 108, 28, 95, 2, 73, 22, 43, 109, 38, 44, 87, 57, 110, 36, 47, 19, 46, 111, 31, 64, 8, 112, 65, 71, 66, 35, 113, 49, 9, 34, 114, 52, 82, 30, 51, 50, 68, 115, 21, 29, 78, 81, 116, 75, 7, 117, 53, 18, 41, 118, 86, 6, 84]
True
[59, 5, 83, 61, 85, 100, 77, 80, 58, 101, 92, 42, 98, 24, 55, 4, 25, 102, 45, 82, 88, 7, 46, 48, 60, 93, 103, 14, 15, 73, 22, 89, 13, 104, 63, 62, 11, 90, 35, 70, 105, 72, 39, 23, 67, 56, 54, 106, 27, 33, 29, 10, 20, 1, 107, 28, 95, 2, 40, 53, 96, 97, 91, 108, 36, 47, 8, 84, 37, 17, 109, 31, 69, 52, 66, 32, 110, 16, 44, 38, 86, 43, 74, 111, 65, 71, 79, 3, 50, 112, 21, 12, 76, 51, 9, 68, 113, 75, 99, 87, 57, 26, 114, 94, 30, 81, 78, 34, 115, 64, 19, 49, 116, 18, 41, 6]
True


In [97]:
x.solution == y.solution

False

# Selection

In [98]:
def random_selection(population):
    return random.choice(population)

In [99]:
def tournament_selection(population, tournament_size):
    tournament = random.sample(population, tournament_size)
    return max(tournament, key = lambda x: x.fitness)

In [100]:
def roulette_selection(population):
    total_fitness = sum([individual.fitness for individual in population])
    selection_probs = [individual.fitness / total_fitness for individual in population]
    return random.choices(population, weights=selection_probs)[0]

In [101]:
def rang_selection(population):
    n = len(population)
    rang_sum = n * (n+1) / 2
    selection_probs = []
    for rang, _ in enumerate(sorted(population, key=lambda x: x.fitness), 1):
        selection_probs.append(rang / rang_sum)
        
    return random.choices(population, weights=selection_probs)[0]

In [102]:
def selection(param, population):
    if param["tournament_size"] is not None:
        return param["selection"](population, param["tournament_size"])
    else:
        return param["selection"](population)

In [103]:
class Example_Individual:
    def __init__(self, fitness, name):
        self.fitness = fitness
        self.name = name

example_population = [Example_Individual(fitness=0.8, name='A'), 
                      Example_Individual(fitness=0.6, name='B'), 
                      Example_Individual(fitness=0.7, name='C'),
                      Example_Individual(fitness=0.8, name='D'), 
                      Example_Individual(fitness=0.9, name='E')]

print(random_selection(example_population).name)
print(tournament_selection(example_population, 3).name)
print(roulette_selection(example_population).name)
print(rang_selection(example_population).name)

D
E
A
D


# Crossover

In [104]:
def order_crossover(parent1, parent2, child1, child2):
    def oc(p1, p2, ch):
        lb, ub = sorted(random.sample(range(len(p1) + 1), 2))
        ch[lb:ub] = p1[lb:ub]

        j = 0
        for i in range(len(p2)):
            if j == lb:
                j = ub + 1

            if j >= len(ch):
                break

            if p2[i] not in ch:
                ch[j] = p2[i]
                j = j + 1 

        return ch
    
    
    child1 = oc(parent1, parent2, child1)
    child2 = oc(parent2, parent1, child2)
    
    return child1, child2

In [105]:
def partially_mapped_crossover(parent1, parent2, child1, child2):
    cutoff_1, cutoff_2 = sorted(random.sample(range(len(parent1) + 1), 2))
    
    child1 = deepcopy(parent1)
    child2 = deepcopy(parent2)
    
    child1[cutoff_1:cutoff_2] = parent2[cutoff_1:cutoff_2]
    child2[cutoff_1:cutoff_2] = parent1[cutoff_1:cutoff_2]

   

    middle_map = {}
    for a, b in zip (child1[cutoff_1:cutoff_2], child2[cutoff_1:cutoff_2]):
        middle_map[a] = middle_map.get(a, 0) + 1
        middle_map[b] = middle_map.get(b, 0) + 1
        
    mapping_order = []
    for key, value in middle_map.items():
        if value != 2:
            mapping_order.append(key)
            
    def find_all_occurrences(lst, item):
        return [i for i, x in enumerate(lst) if x == item]    
          
    def replace_a_b(x_pos, y, child, cutoff_1, cutoff_2):
        for i in x_pos:
            if i not in range(cutoff_1, cutoff_2):
                child[i] = y
                break 
                   
        return child
        
    def replace_a_b_child(a, a_pos, b, b_pos, child, cutoff_1, cutoff_2):
        if len(a_pos) != 0:
             return replace_a_b(a_pos, b, child, cutoff_1, cutoff_2)
        else:
            return replace_a_b(b_pos, a, child, cutoff_1, cutoff_2)
        
    for i in range(0, len(mapping_order)-1, 2):
        a = mapping_order[i]
        b = mapping_order[i+1]

        a_child1_positions = find_all_occurrences(child1, a)
        a_child2_positions = find_all_occurrences(child2, a)
        
        
        b_child1_positions = find_all_occurrences(child1, b)
        b_child2_positions = find_all_occurrences(child2, b)
        
        child1 = replace_a_b_child(a, a_child1_positions, b, b_child1_positions, child1, cutoff_1, cutoff_2)
        child2 = replace_a_b_child(a, a_child2_positions, b, b_child2_positions, child2, cutoff_1, cutoff_2)

    return child1, child2

[1 | 2 3 4 | 5]  
[5 | 4 3 1 | 2]   

[1 | 4 3 1 | 5]   
[5 | 2 3 4 | 2]   

4-2, 3-3, 1-4

1: 1   
2: 1   
3: 2   
4: 2  
1 -> 2  

[2 | 1 3 4 | 5]    
[5 | 2 3 4 | 1]    

In [106]:
def best_route_better_adjustment_crossover(individual, parent1, parent2, child1, child2):
    # n/2 best from parent1 into first n/2 of child1
    # the rest elements are from parent2 
    # the positions of vehicles are fixed
        
    def create_child(p1, p2, ch1):
        p1_routes = individual.get_routes()
        p1_sorted = sorted(p1_routes, key = lambda route: individual.route_fitness(route))

        # copy half of the best routes from parent1 to child 1
        best_routes_index = 0
        i = 0
        node_index = 0
        while best_routes_index <= len(p1_sorted) / 2:
            node = ch1[node_index]
            if node <= individual.num_of_cities and i < len(p1_sorted[best_routes_index]):
                ch1[node_index] = p1_sorted[best_routes_index][i]
                i = i + 1
            else:
                best_routes_index = best_routes_index + 1
                i = 0

            node_index = node_index + 1

        # copy elements from parent2 that aren't in child so far
        p2_index = 0
        while node_index < len(ch1):
            node = ch1[node_index]
            if node <= individual.num_of_cities:
                p2_node = p2[p2_index]
                if p2_node > individual.num_of_cities:
                    p2_index = p2_index + 1
                    p2_node = p2[p2_index]
                
                if p2_node not in ch1[:node_index]:
                    ch1[node_index] = p2_node
                p2_index = p2_index + 1

            node_index = node_index + 1
            
        return ch1
    
    child1 = create_child(parent1, parent2, child1)
    child2 = create_child(parent2, parent1, child2)
    return child1, child2

In [107]:
def crossover(param, parent1, parent2, child1, child2):
    if param["individual"] is not None:
        return param["crossover"](param["individual"], parent1, parent2, child1, child2)
    else:
        return param["crossover"](parent1, parent2, child1, child2)

# Mutation

In [108]:
def swap_mutation(individual):
    l, r = sorted(random.sample(range(len(individual)), 2))
    individual[l], individual[r] = individual[r], individual[l]
    
    return individual

In [109]:
def invert_mutation(individual):
    l, r = sorted(random.sample(range(len(individual) + 1), 2))
    chosen = individual[l:r]
    chosen.reverse()
    individual[l:r] = chosen
    
    return individual

In [110]:
def shaking_mutation(individual):
    l, r = sorted(random.sample(range(len(individual) + 1), 2))
    chosen = individual[l:r]
    random.shuffle(chosen)
    individual[l:r] = chosen
    
    return individual

In [111]:
def mutation(param, individual, mutation_prob):
    if random.random() < mutation_prob:
        individual = param(individual)
        
    return individual

# Fix solution



    "An adaptive large neighborhood search heuristic for the vehicle routing problem with time windows" by C. R. Castro, M. G. C. Resende, and A. A. Viana. (2012)
        This paper presents an adaptive large neighborhood search (ALNS) heuristic for the VRPTW, which includes an insertion-based repair mechanism.

    "A hybrid genetic algorithm for the vehicle routing problem with time windows" by Y. Liang and J. Zhang. (2006)
        The authors propose a hybrid genetic algorithm that integrates an insertion-based repair method for the VRPTW.

    "An adaptive memory algorithm for a class of vehicle routing problems with time windows" by M. Gendreau, G. Laporte, and F. Semet. (2006)
        This paper introduces an adaptive memory algorithm for vehicle routing problems, including the VRPTW, which utilizes insertion-based repair techniques.

    "An adaptive algorithm for the vehicle routing problem with time windows" by M. Gendreau, G. Laporte, and F. Semet. (2002)
        The authors propose an adaptive algorithm for the VRPTW that employs insertion-based repair strategies to improve solution quality.

    "An adaptive large neighborhood search heuristic for the vehicle routing problem with time windows" by T. G. Crainic, M. Gendreau, and J. Potvin. (2000)
        This paper introduces an adaptive large neighborhood search heuristic for the VRPTW, which includes insertion-based repair procedures to handle infeasible solutions.

ideja: citye koji prave unfeasible rute treba izvuci i staviti u removelistu i onda ih rasporedjujemo tamo gde mozemo, ako ih je nemoguce rasporediti pravimo novu rutu od njih 
ili cvorove u unfeasible rutama preuredimo da budu feasible 


In [118]:
def insertion_based_repair(individual):
    if (individual.is_feasable()):
        return individual
        
    routes = individual.get_routes()
    unfeasible_routes = []
    for route in routes:
        _,_,_, is_unfeasable = individual.route_fitness(route)
        if is_unfeasable:
            unfeasible_routes.append(route)
            routes.remove(route)
            
    removed_cities_list = []
    for route in unfeasible_routes:
        sorted_route = route.sort(key = lambda x: (individual.data[x]["ready_time"], individual.data[x]["due_time"]))
        _, _, _, is_unfeasable = individual.route_fitness(sorted_route)
        
        if is_unfeasable:
            current_time  = 0
            previous_city = 0
            remaining_capacity = individual.capacity
            
            # find and eliminate unfeasable cities
            for current_city in sorted_route:
                if current_time + individual.calc_distance(individual.data[previous_city], individual.data[current_city]) > \
                   individual.data[current_city]["due_time"] or individual.data[current_city]["demand"] > remaining_capacity:
                        sorted_route.remove(current_city)
                        removed_cities_list.append(current_city)
                else:
                    current_time += individual.calc_distance(individual.data[previous_city], individual.data[current_city])
                    remaining_capacity -= individual.data[current_city]["demand"]
                    previous_city = current_city
                    
        route = deepcopy(sorted_route)
        routes.append(route)
        
    # first try: insert if possible in existing route
    if len(removed_cities_list) > 0:
        for city_index in removed_cities_list:
            is_inserted = False
            for route in routes:            
                for i in range(len(route)):
                    route_copy = deepcopy(route)
                    route_copy.insert(i, city_index)
                    
                    _,_,_, is_unfeasable = individual.route_fitness(route_copy)
                    if not is_unfeasable:
                        route = deepcopy(route_copy)
                        inserted = True
                        removed_cities_list.remove(city_index)
                        break
                        
                if inserted:
                    break

    # second try: create new routes 
    if len(removed_cities_list) > 0 and individual.num_of_vehicles - len(routes) > 0:
        individual.generate_solution_nearest_neighbors(routes, removed_cities_list)
    
    return individual

# Genetic algorithm

In [119]:
def genetic_algorithm(params):
    
    data = params["data"]
    capacity = params["capacity"]
    num_of_vehicles = params["num_of_vehicles"]
    service_time = params["service_time"]
    population_size = params["population_size"]
    num_generations = params["num_generations"]
    elitism_size = params["elitism_size"]
    tournament_size = params["tournament_size"]
    selection_params = params["selection"]
    crossover_param = params["crossover"]
    mutation_params = params["mutation"]
    mutation_prob = params["mutation_prob"]
    
    population = [Individual(data, capacity, num_of_vehicles, len(data)-1, service_time ) for _ in range(population_size)]
    print([x.fitness for x in population])
    new_population = deepcopy(population)
  
    crossover_params = { "crossover" : crossover_param, 
                         "individual" : population[0] if crossover_param.__name__ == "best_route_better_adjustment_crossover" else None }
    best_solutions = []
    for i in range(num_generations):
        population.sort(key = lambda x: x.fitness)
        print([x.fitness for x in population])
        best_solutions.append(population[0])
        new_population[:elitism_size] = population[:elitism_size]
        for j in range(elitism_size, population_size, 2):
            parent1 = selection(selection_params, population)
            parent2 = selection(selection_params, population)
            
            while(parent1 == parent2):
                parent2 = selection(selection_params, population)

            
            new_population[j].solution, new_population[j+1].solution = crossover(crossover_params, 
                                                                                 parent1.solution, 
                                                                                 parent2.solution, 
                                                                                 new_population[j].solution, 
                                                                                 new_population[j+1].solution)
                
            
            new_population[j].solution = mutation(mutation_params, new_population[j].solution, mutation_prob)
            new_population[j+1].solution = mutation(mutation_params, new_population[j+1].solution, mutation_prob)

            insertion_based_repair(new_population[j])
            insertion_based_repair(new_population[j+1])

            new_population[j].fitness = new_population[j].calc_fitness()
            new_population[j+1].fitness = new_population[j+1].calc_fitness()

        population = deepcopy(new_population)
        
    
    return min(population, key = lambda x: x.fitness), best_solutions

In [120]:
POPULATION_SIZE = 1000
ELITISIM_SIZE = 100
MUTATION_PROB = 0.1
TOURNAMENT_SIZE = 300
NUM_GENERATIONS = 100
CAPACITY = 300
SELECTION = rang_selection
CROSSOVER = order_crossover
MUTATION = shaking_mutation
NUM_OF_VEHICLES = 50
SERVICE_TIME = 10

params = {
    "data" : input1,
    "population_size" : POPULATION_SIZE,
    "elitism_size" : ELITISIM_SIZE,
    "mutation_prob" : MUTATION_PROB,
    "tournament_size" : TOURNAMENT_SIZE,
    "num_generations" : NUM_GENERATIONS,
    "capacity" : CAPACITY,
    "selection" : { "selection" : SELECTION, 
                    "tournament_size" : TOURNAMENT_SIZE if SELECTION.__name__ == "tournament_selection" else None
                  },
    "crossover" : CROSSOVER,
    "mutation" : MUTATION,
    "num_of_vehicles" : NUM_OF_VEHICLES,
    "service_time" : SERVICE_TIME
}

ga_order_crossover, best_solutions_order_crossover = genetic_algorithm(params)

# params["crossover"] = partially_mapped_crossover

# ga_pmc, best_solutions_pmc = genetic_algorithm(params)

# params["crossover"] = best_route_better_adjustment_crossover

# ga_brbac, best_solutions_brbac = genetic_algorithm(params)


[3503.53, 3464.342, 3158.389, 3462.705, 3541.6879999999996, 3359.543, 3527.5959999999995, 3509.4919999999997, 3646.2040000000006, 3365.428000000001, 3443.948, 3423.8100000000004, 3506.683, 3410.104, 3433.683, 3405.495000000001, 3389.3830000000003, 3509.866, 3404.05, 3358.5480000000002, 3339.146, 3312.1410000000005, 3462.57, 3518.6010000000006, 3259.1669999999995, 3297.679, 3503.3200000000006, 3372.014, 3510.473, 3421.638, 3419.188, 3530.686, 3396.1250000000005, 3575.7470000000003, 3163.526, 3417.8250000000007, 3305.5499999999997, 3383.7390000000005, 3477.2219999999993, 3493.948, 3458.9150000000004, 3540.0890000000004, 3295.2709999999997, 3277.562, 3368.105, 3483.783, 3571.08, 3423.352999999999, 3277.777, 3525.555, 3695.4110000000005, 3282.9679999999994, 3419.3000000000006, 3494.321999999999, 3424.3500000000004, 3358.306, 3264.404, 3310.1150000000002, 3408.798, 3322.2330000000006, 3374.8840000000005, 3375.463000000001, 3487.841, 3305.992000000001, 3306.37, 3756.957, 3326.4959999999996, 

time window violation for route: [73, 40, 20, 11, 62, 21, 75, 99, 6]
time window violation for route: [4, 80, 16, 98, 22, 55, 100]
time window violation for route: [13, 89, 92, 37, 20, 62, 60]
time window violation for route: [66, 55, 2, 31, 30, 34, 35, 47, 19]
time window violation for route: [73, 85, 43, 59, 5, 55, 4, 25, 83, 16, 86, 40, 27, 79, 3, 33, 31, 44, 61, 6, 68, 34, 81, 9, 51, 53, 56, 29, 41, 84]
time window violation for route: [61, 85, 80, 44, 43, 88, 10, 100, 58]
time window violation for route: [59, 58, 88, 7, 38, 13, 93]
time window violation for route: [58, 13, 89, 98, 25]
time window violation for route: [70, 24, 50, 13, 55, 4, 72, 51, 26, 54, 76, 45, 83, 16, 85, 43, 74, 100]
time window violation for route: [51, 35, 42, 1, 48, 72, 20, 94]
time window violation for route: [13, 91, 32, 60, 66, 96, 71, 50, 26, 9, 30, 2, 40, 4, 95, 98, 86, 21, 57, 37, 52, 65, 51, 20, 82, 62, 67, 73, 55, 54, 24]
time window violation for route: [59, 5, 68, 77, 92, 38, 16, 42, 13, 99, 85, 

time window violation for route: [74, 93, 22, 56, 98, 83, 24, 50, 68, 95, 96, 85, 40, 54, 26, 13, 89, 58]
time window violation for route: [74, 16, 93, 5, 44, 84]
time window violation for route: [70, 86, 22, 20, 1, 59, 5, 15, 73, 41, 56, 4, 25, 87, 85, 63, 74, 94, 72, 99, 60, 14, 96, 39, 6, 62]
time window violation for route: [60, 59, 5, 56, 22, 42, 61, 85, 43, 45, 68, 58, 14, 91, 83, 7, 37, 73, 99, 6, 44, 84, 38, 89, 27, 28, 12, 76, 3, 34, 35, 80]
time window violation for route: [83, 3, 15, 73, 1, 46, 68, 24, 27, 33, 4, 28, 2, 51, 12, 76, 79, 54, 23, 67, 29, 40, 53, 61, 18]
time window violation for route: [54, 70, 32, 29, 78, 95, 9, 20, 66, 71, 11, 84, 18]
time window violation for route: [44, 15, 6, 97, 100, 14, 54, 2, 21, 73, 40, 50, 68, 31, 53, 30, 10, 20, 1, 60, 93]
time window violation for route: [20, 84, 95, 63, 62, 48, 72, 26, 74, 35]
time window violation for route: [89, 95, 70, 19, 100, 29, 37, 79, 49, 39, 22, 56, 74, 52, 96, 99, 94, 43, 23, 75, 44, 46, 17, 60, 93]
time 

time window violation for route: [56, 37, 83, 35, 1, 77]
time window violation for route: [77, 74, 80, 54, 46, 72, 40, 73, 56, 79, 3, 2, 19, 53, 31, 11, 20, 21, 23, 29, 78]
time window violation for route: [100, 79, 33, 29, 81]
time window violation for route: [35, 77, 80, 83, 97, 13, 73, 38, 70, 16, 68, 90, 51, 75, 76, 30, 85, 22]
time window violation for route: [77, 50, 87, 40, 75, 16, 53, 96, 60, 89, 58]
time window violation for route: [58, 59, 68, 77, 45, 83, 88, 5, 4, 82]
time window violation for route: [4, 58, 91, 46, 55, 80, 56, 33, 27, 28, 37, 25, 3, 68, 24, 77]
time window violation for route: [94, 100, 89, 99, 6, 45, 90, 13, 10, 32, 11, 97, 50, 4, 51, 79, 86]
time window violation for route: [100, 89, 77, 80, 3, 60, 72, 95, 2, 50, 81, 8, 87, 41, 57, 67, 53]
time window violation for route: [8, 11, 65, 57, 59, 82, 96, 21, 40, 94]
time window violation for route: [59, 56, 4, 25, 77, 96, 32, 62, 88, 90, 10, 1, 89, 58]
time window violation for route: [26, 94, 83, 61, 55, 25, 

time window violation for route: [5, 3, 93, 18, 97, 25, 4, 15, 77, 19, 91, 8, 84, 56, 54, 21, 29, 38]
time window violation for route: [5, 56, 4, 77, 54, 83, 16, 85, 14, 89, 70, 73, 96, 32, 43, 74, 58]
time window violation for route: [45, 83, 77, 55, 54, 9, 16, 85, 26, 4, 25]
time window violation for route: [98, 16, 58, 45, 83, 5, 96, 13, 89]
time window violation for route: [2, 21, 57, 90, 10, 32, 77]
time window violation for route: [23, 70, 72]
time window violation for route: [12, 76, 3, 34, 35, 51, 50, 24, 25, 71, 9, 20, 98, 6]
time window violation for route: [20, 24, 33, 1, 70, 36, 5, 23, 21, 35, 39, 75, 27, 28, 10, 32, 83, 37, 69, 47, 41, 18, 67]
time window violation for route: [10, 92, 42, 98]
time window violation for route: [82, 88, 46, 13, 72, 39, 75, 95, 40, 50, 47, 52, 37, 17, 49, 18, 16]
time window violation for route: [13, 97, 89, 58, 16, 93, 86, 72, 40, 49, 11, 59, 5, 83, 7, 8, 46, 77]
time window violation for route: [58, 7, 46, 74, 32, 60]
time window violation f

...

time window violation for route: [81, 61, 35, 42, 36]
time window violation for route: [22, 46, 23]
time window violation for route: [43, 10, 66, 49, 8, 35, 26]
time window violation for route: [51, 78, 72, 30, 50]
time window violation for route: [79, 20, 56, 60, 95, 44, 3, 19, 36, 80, 18, 42, 40, 17, 96, 25, 82, 49, 23, 83, 54, 78]
time window violation for route: [45, 81, 28, 20, 23, 72]
time window violation for route: [15, 60, 12, 38, 14, 75, 64, 50, 34, 45]
time window violation for route: [100, 16, 11, 33, 17, 24, 21, 30]
time window violation for route: [45, 28, 82, 50, 73, 13, 56, 63, 90, 80, 77, 6, 32]
time window violation for route: [24, 21, 93, 99, 53, 74, 65, 64, 37, 79]
time window violation for route: [58, 21, 34, 69, 28, 51, 9, 16, 88]
time window violation for route: [51, 25, 84, 69]
time window violation for route: [3, 81, 84, 15, 12]
time window violation for route: [4, 86, 72]
time window violation for route: [21, 53, 48, 6, 54, 91, 27, 59, 41, 18, 40, 77]
time win

[-7316.0250000000015, -7052.037999999999, -6835.546, -6726.332000000002, -6677.937999999999, -6666.948000000002, -6550.808000000002, -6539.271000000001, -6538.043000000001, -6511.087000000001, -6482.991, -6482.289000000001, -6462.9529999999995, -6455.959999999999, -6414.048999999999, -6405.580999999999, -6405.257, -6388.804, -6306.099000000002, -6304.724999999999, -6286.47, -6279.2040000000015, -6261.116, -6259.560999999998, -6247.753, -6221.990000000001, -6201.157, -6199.371999999999, -6184.0419999999995, -6183.566000000001, -6173.975999999998, -6166.567000000001, -6161.822000000002, -6126.29, -6122.522999999998, -6105.303, -6104.365000000002, -6100.727000000001, -6097.763000000001, -6093.0740000000005, -6083.4349999999995, -6080.849000000001, -6080.039000000001, -6066.706000000002, -6061.563, -6040.6280000000015, -6000.529, -5993.968000000002, -5983.393000000001, -5957.352, -5945.009999999999, -5928.594999999999, -5926.5160000000005, -5922.5560000000005, -5912.540000000001, -5908.107

time window violation for route: [67, 5, 93, 36, 100, 59, 42, 41, 47]
time window violation for route: [73, 86, 99, 97, 60, 34, 17, 63, 32]
time window violation for route: [97, 65, 20, 87, 13, 21, 81, 7, 92, 50, 73, 10, 15, 36, 2, 53, 77, 17, 18, 34, 93, 71, 27, 19, 84, 50, 11, 96, 57]
time window violation for route: [24, 28, 26, 23, 71, 74]
time window violation for route: [24, 51, 9, 77, 7, 64, 13, 83, 67, 69]
time window violation for route: [25, 42]
time window violation for route: [79, 12, 30, 89, 67]
time window violation for route: [36, 85, 84, 39, 59, 83, 75, 23, 21, 81, 99, 35, 15, 54]
time window violation for route: [45, 97, 62, 90, 6, 83, 2, 33, 27]
time window violation for route: [83, 32, 87, 54, 17, 53, 86, 91]
time window violation for route: [43, 47, 28]
time window violation for route: [62, 88, 29, 40, 51, 52, 30, 2, 85, 4]
time window violation for route: [78, 67, 15, 66, 33, 62, 2]
time window violation for route: [14, 85, 59, 3, 61, 44, 47, 69, 39, 2, 33, 64, 29,

time window violation for route: [94, 62, 50, 87, 86, 21, 10, 23, 92, 32, 26, 38, 44, 73, 82, 17, 36, 3]
time window violation for route: [85, 39, 20, 16, 48, 10, 51, 57, 79, 46]
time window violation for route: [19, 35, 58, 12, 25]
time window violation for route: [51, 81, 29, 10, 16, 73]
time window violation for route: [92, 78, 96, 77, 4, 64, 25, 94, 31, 90, 66, 19, 89, 86, 37]
time window violation for route: [97, 72, 16, 38, 88, 61, 70, 54, 20, 40, 82, 78, 36, 77, 17, 76, 46, 95, 48, 55, 63, 79, 5, 65, 4, 25]
time window violation for route: [55, 79, 71, 32, 41]
time window violation for route: [58, 29, 7, 13, 57, 54, 85, 71]
time window violation for route: [98, 69, 62, 73]
time window violation for route: [91, 37, 52, 36, 30, 65, 18]
time window violation for route: [88, 86, 62, 51, 32]
time window violation for route: [21, 99, 51, 75, 82]
time window violation for route: [6, 36, 47, 54, 61]
time window violation for route: [23, 69, 32]
time window violation for route: [8, 67, 8

time window violation for route: [94, 58, 77, 86, 2]
time window violation for route: [56, 76, 6, 79, 99, 13, 53]
time window violation for route: [27, 6, 44, 33]
time window violation for route: [97, 12, 96, 84]
time window violation for route: [9, 81, 95]
time window violation for route: [20, 1, 52, 57, 84, 6, 51, 18]
time window violation for route: [49, 62]
time window violation for route: [9, 57, 80, 69, 24]
time window violation for route: [54, 51, 58, 66, 91, 21, 55]
time window violation for route: [14, 61, 23, 32, 17, 59, 8, 42, 60, 12, 1, 47, 18, 44, 74, 4, 33, 13, 27, 2, 37, 26, 73, 77, 89, 86, 52, 50, 40, 64, 9, 90]
time window violation for route: [12, 51, 45, 63, 3, 30]
time window violation for route: [98, 91, 38, 36, 74, 2, 94, 51, 24]
time window violation for route: [92, 74, 87, 4, 82, 91]
time window violation for route: [16, 98, 97, 27, 50]
time window violation for route: [77, 4, 25, 64, 54, 1, 29, 67]
time window violation for route: [23, 68, 99, 66, 20, 85, 80]
t

In [121]:
ga_order_crossover.is_feasable()

time window violation for route: [44, 59, 75, 66, 51, 65, 80]


False

In [124]:
print(sum(1 for route in ga_order_crossover.get_routes() if len(route) > 0))
print(len(ga_order_crossover.get_routes()))
print(ga_order_crossover.fitness)

14
14
-7316.0250000000015


In [123]:
ga_pmc.is_feasable()

NameError: name 'ga_pmc' is not defined

In [ ]:
ga_brbac.is_feasable()

In [ ]:
ga_brbac.solution == ga_pmc.solution

egzaktan, grafovi, viseciljna, reference, prezentacija i pdf



# Graphs

In [ ]:
def plot_cities(x_coordinates, y_coordinates, dataset_name):
    plt.figure(figsize=(8, 6))
    plt.scatter(x_coordinates[1:], y_coordinates[1:], color='red', label='cities')
    plt.scatter(x_coordinates[0], y_coordinates[0], color='blue', label='Depot') 
    plt.xlabel('X')
    plt.ylabel('Y')
    plt.title('City Coordinates for ' + dataset_name)
    plt.legend()
    plt.grid(True)
    plt.show()

In [ ]:
x_input1 = [x["x"] for x in input1]
y_input1 = [x["y"] for x in input1]

x_input2 = [x["x"] for x in input2]
y_input2 = [x["y"] for x in input2]

x_input3 = [x["x"] for x in input3]
y_input3 = [x["y"] for x in input3]


plot_cities(x_input1, y_input1, "input_1")


In [ ]:
#Best solution routes 
def plot_best_solution(x, title):
    plt.figure(figsize=(8, 6))
    routes = x.get_routes()
    for route in routes:
        x_points  = np.array([x.depot["x"]])
        x_points = np.append(x_points, [x.data[i]["x"] for i in route], axis = 0)
        x_points = np.append(x_points, [x.depot["x"]], axis = 0)
        y_points  = np.array([x.depot["y"]])
        y_points = np.append(y_points, [x.data[i]["y"] for i in route], axis = 0)
        y_points = np.append(y_points, [x.depot["y"]], axis = 0)
        

        plt.plot(x_points, y_points)
    
    plt.title(title)
    plt.show


In [ ]:
plot_best_solution(ga_order_crossover, "Best Solution Routes OC")
plot_best_solution(ga_pmc, "Best Solution Routes PMC")
plot_best_solution(ga_brbac, "Best Solution Routes BRBAC") 

In [ ]:
def best_solution_evolution(solutions, title, info):
    plt.figure(figsize=(8, 6))
    y_points = [[] for _ in range(len(solutions))]
    i = 0
    for solution in solutions:
        y_points[i] = [x.fitness for x in solution]
        i+=1
    
    for i,y in enumerate(y_points):
        plt.plot(np.array(y), label = info[i])
    plt.title(title)
    plt.ylabel("fitness")
    plt.xlabel("generation")
    plt.legend()
    plt.show()

In [ ]:
best_solution_evolution([best_solutions_order_crossover,best_solutions_brbac, best_solutions_pmc], "The Effect Of Crossover Function On Fitness Using Nearest Neighbour Initialization", ["Order Crossover", "Best Route Better Adjustment Crossover", "Partially Mapped Crossover"])